### Import Required Libraries and Set Up Environment Variables

In [2]:
# Dependencies
import requests
import time
from dotenv import load_dotenv
import os
import pandas as pd
import json
import os
from datetime import datetime
## Load the NASA_API_KEY from the env file
load_dotenv()
NASA_API_KEY = os.getenv('NASA_API_KEY')

### CME Data

In [72]:
# Set the base URL to NASA's DONKI API:
base_url = "https://api.nasa.gov/DONKI/"

# Set the specifier for CMEs:
CME = "CME"

# Search for CMEs published between a begin and end date
startDate = "2013-05-01"
endDate   = "2015-05-01"                    #I changed this because anything greater and I'd get timeout errors

# Build URL for CME
cme_query_url = f'{base_url}{CME}?startDate={startDate}&endDate={endDate}&api_key={NASA_API_KEY}'
print(cme_query_url)

https://api.nasa.gov/DONKI/CME?startDate=2013-05-01&endDate=2015-05-01&api_key=v3cb6u2K4SofJWUFcnupS80ZgFMhbT0iGHo9nPBf


In [410]:
# Make a "GET" request for the CME URL and store it in a variable named cme_response
cme_response = requests.get(cme_query_url)

In [411]:
# Convert the response variable to json and store it as a variable named cme_json
cme_json = cme_response.json()

In [412]:
# Preview the first result in JSON format
# Use json.dumps with argument indent=4 to format data
print(json.dumps(cme_json, indent=4))

[
    {
        "activityID": "2013-05-01T03:12:00-CME-001",
        "catalog": "M2M_CATALOG",
        "startTime": "2013-05-01T03:12Z",
        "instruments": [
            {
                "displayName": "SOHO: LASCO/C2"
            },
            {
                "displayName": "SOHO: LASCO/C3"
            },
            {
                "displayName": "STEREO A: SECCHI/COR2"
            },
            {
                "displayName": "STEREO B: SECCHI/COR2"
            }
        ],
        "sourceLocation": "",
        "activeRegionNum": null,
        "note": "",
        "submissionTime": "2013-08-07T16:54Z",
        "versionId": 1,
        "link": "https://webtools.ccmc.gsfc.nasa.gov/DONKI/view/CME/2349/-1",
        "cmeAnalyses": [
            {
                "isMostAccurate": true,
                "time21_5": "2013-05-01T07:07Z",
                "latitude": 12.0,
                "longitude": -120.0,
                "halfAngle": 36.0,
                "speed": 860.0,
        

In [471]:
# Convert cme_json to a Pandas DataFrame 
cme_df =  pd.DataFrame(cme_json)
cme_df.info()
# Keep only the columns: activityID, startTime, linkedEvents
cme_df = cme_df[['activityID','startTime','linkedEvents']]
cme_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1174 entries, 0 to 1173
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   activityID       1174 non-null   object 
 1   catalog          1174 non-null   object 
 2   startTime        1174 non-null   object 
 3   instruments      1174 non-null   object 
 4   sourceLocation   1174 non-null   object 
 5   activeRegionNum  146 non-null    float64
 6   note             1174 non-null   object 
 7   submissionTime   1174 non-null   object 
 8   versionId        1174 non-null   int64  
 9   link             1174 non-null   object 
 10  cmeAnalyses      1140 non-null   object 
 11  linkedEvents     230 non-null    object 
dtypes: float64(1), int64(1), object(10)
memory usage: 110.2+ KB


activityID          startTime  \
0  2013-05-01T03:12:00-CME-001  2013-05-01T03:12Z   
1  2013-05-02T05:24:00-CME-001  2013-05-02T05:24Z   
2  2013-05-02T14:36:00-CME-001  2013-05-02T14:36Z   
3  2013-05-03T18:00:00-CME-001  2013-05-03T18:00Z   
4  2013-05-03T22:36:00-CME-001  2013-05-03T22:36Z   

                                      linkedEvents  
0  [{'activityID': '2013-05-04T04:52:00-IPS-001'}]  
1                                             None  
2                                             None  
3                                             None  
4  [{'activityID': '2013-05-07T04:37:00-IPS-001'}]

In [472]:
# Notice that the linkedEvents column allows us to identify the corresponding GST
# Remove rows with missing 'linkedEvents' since we won't be able to assign these to GSTs
cme_df.dropna(subset=['linkedEvents'], inplace=True)
cme_df.info()
cme_df.head(10)

<class 'pandas.core.frame.DataFrame'>
Index: 230 entries, 0 to 1171
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   activityID    230 non-null    object
 1   startTime     230 non-null    object
 2   linkedEvents  230 non-null    object
dtypes: object(3)
memory usage: 7.2+ KB


activityID          startTime  \
0   2013-05-01T03:12:00-CME-001  2013-05-01T03:12Z   
4   2013-05-03T22:36:00-CME-001  2013-05-03T22:36Z   
7   2013-05-09T19:29:00-CME-001  2013-05-09T19:29Z   
10  2013-05-13T02:54:00-CME-001  2013-05-13T02:54Z   
13  2013-05-13T16:18:00-CME-001  2013-05-13T16:18Z   
14  2013-05-14T01:30:00-CME-001  2013-05-14T01:30Z   
15  2013-05-15T02:18:00-CME-001  2013-05-15T02:18Z   
17  2013-05-17T09:24:00-CME-001  2013-05-17T09:24Z   
18  2013-05-18T03:24:00-CME-001  2013-05-18T03:24Z   
20  2013-05-22T09:12:00-CME-001  2013-05-22T09:12Z   

                                         linkedEvents  
0     [{'activityID': '2013-05-04T04:52:00-IPS-001'}]  
4     [{'activityID': '2013-05-07T04:37:00-IPS-001'}]  
7     [{'activityID': '2013-05-12T23:30:00-IPS-001'}]  
10  [{'activityID': '2013-05-13T01:53:00-FLR-001'}...  
13  [{'activityID': '2013-05-13T15:40:00-FLR-001'}...  
14    [{'activityID': '2013-05-14T01:00:00-FLR-001'}]  
15  [{'activityID': '2013-05-15T01:25:00-FLR-001'}...  
17    [{'activityID': '2013-05-19T22:20:00-IPS-001'}]  
18    [{'activityID': '2013-05-19T18:53:00-IPS-001'}]  
20    [{'activityID': '2013-05-25T20:00:00-IPS-001'}]

In [473]:
# Notice that the linkedEvents sometimes contains multiple events per row
# Write a nested for loop that iterates first over each row in the cme DataFrame (using the index)
# and then iterates over the values in 'linkedEvents' 
# and adds the elements individually to a list of dictionaries where each row is one element 

# Initialize an empty list to store the expanded rows
expanded_rows = []

# Iterate over each index in the DataFrame
for i in cme_df.index:
    activityID = cme_df.loc[i,'activityID']
    startTime = cme_df.loc[i,'startTime']
    linkedEvents = cme_df.loc[i,'linkedEvents']

    # Iterate over each dictionary in the list
    for item in linkedEvents:
        # Append a new dictionary to the expanded_rows list for each dictionary item and corresponding 'activityID' and 'startTime' value
        expanded_rows.append({
            'activityID': activityID,
            'startTime': startTime,
            'linkedEvents': item
        })
# Create a new DataFrame from the expanded rows
expanded_cme_df = pd.DataFrame(expanded_rows)
expanded_cme_df.info()
expanded_cme_df.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 337 entries, 0 to 336
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   activityID    337 non-null    object
 1   startTime     337 non-null    object
 2   linkedEvents  337 non-null    object
dtypes: object(3)
memory usage: 8.0+ KB


activityID          startTime  \
0  2013-05-01T03:12:00-CME-001  2013-05-01T03:12Z   
1  2013-05-03T22:36:00-CME-001  2013-05-03T22:36Z   
2  2013-05-09T19:29:00-CME-001  2013-05-09T19:29Z   
3  2013-05-13T02:54:00-CME-001  2013-05-13T02:54Z   
4  2013-05-13T02:54:00-CME-001  2013-05-13T02:54Z   

                                    linkedEvents  
0  {'activityID': '2013-05-04T04:52:00-IPS-001'}  
1  {'activityID': '2013-05-07T04:37:00-IPS-001'}  
2  {'activityID': '2013-05-12T23:30:00-IPS-001'}  
3  {'activityID': '2013-05-13T01:53:00-FLR-001'}  
4  {'activityID': '2013-05-13T04:12:00-SEP-001'}

In [463]:
print(type(linkedEvents))

<class 'list'>


In [474]:
# Create a function called extract_activityID_from_dict that takes a dict as input such as in linkedEvents
# and verify below that it works as expected using one row from linkedEvents as an example
# Be sure to use a try and except block to handle errors
#input_dict = expanded_df['linkedEvents']
#expanded_cme_df['linkedEvents'] = expanded_cme_df['linkedEvents'].apply(lambda x: x[0] if isinstance(x, list) and len(x) > 0 else {})
def extract_activityID_from_dict(input_dict):
    
        # Log the error or print it for debugging
    try:
       
        if isinstance(input_dict, list) and len(input_dict) > 0 and isinstance(input_dict[0], dict):
            return input_dict[0].get('activityID')
        elif isinstance(input_dict, dict):
            return input_dict.get('activityID')
        else:
            raise TypeError("Input is not a dictionary")
        
    except Exception as e:
        print(f"Error: {e}")
        return None

extract_activityID_from_dict(linkedEvents)

'2015-05-05T17:40:00-IPS-001'

In [476]:
# Apply this function to each row in the 'linkedEvents' column (you can use apply() and a lambda function)
# and create a new column called 'GST_ActivityID' using loc indexer:
expanded_cme_df['GST_ActivityID'] = expanded_cme_df['linkedEvents'].apply(extract_activityID_from_dict)
#lambda x: extracted_activityID_from_dict
expanded_cme_df.info()
expanded_cme_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 337 entries, 0 to 336
Data columns (total 4 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   activityID      337 non-null    object
 1   startTime       337 non-null    object
 2   linkedEvents    337 non-null    object
 3   GST_ActivityID  337 non-null    object
dtypes: object(4)
memory usage: 10.7+ KB


activityID          startTime  \
0  2013-05-01T03:12:00-CME-001  2013-05-01T03:12Z   
1  2013-05-03T22:36:00-CME-001  2013-05-03T22:36Z   
2  2013-05-09T19:29:00-CME-001  2013-05-09T19:29Z   
3  2013-05-13T02:54:00-CME-001  2013-05-13T02:54Z   
4  2013-05-13T02:54:00-CME-001  2013-05-13T02:54Z   

                                    linkedEvents               GST_ActivityID  
0  {'activityID': '2013-05-04T04:52:00-IPS-001'}  2013-05-04T04:52:00-IPS-001  
1  {'activityID': '2013-05-07T04:37:00-IPS-001'}  2013-05-07T04:37:00-IPS-001  
2  {'activityID': '2013-05-12T23:30:00-IPS-001'}  2013-05-12T23:30:00-IPS-001  
3  {'activityID': '2013-05-13T01:53:00-FLR-001'}  2013-05-13T01:53:00-FLR-001  
4  {'activityID': '2013-05-13T04:12:00-SEP-001'}  2013-05-13T04:12:00-SEP-001

In [477]:
expanded_cme_df['GST_ActivityID'].isna().sum()

0

In [478]:
# Remove rows with missing GST_ActivityID, since we can't assign them to GSTs:
expanded_cme_df.dropna(subset=['GST_ActivityID'], inplace=True)

In [479]:
# print out the datatype of each column in this DataFrame:
expanded_cme_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 337 entries, 0 to 336
Data columns (total 4 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   activityID      337 non-null    object
 1   startTime       337 non-null    object
 2   linkedEvents    337 non-null    object
 3   GST_ActivityID  337 non-null    object
dtypes: object(4)
memory usage: 10.7+ KB


In [480]:
# Convert the 'GST_ActivityID' column to string format 
expanded_cme_df['GST_ActivityID'] = expanded_cme_df['GST_ActivityID'].astype(str)

# Convert startTime to datetime format  
expanded_cme_df['startTime'] = pd.to_datetime(expanded_cme_df['startTime'])

# Rename startTime to startTime_CME and activityID to cmeID
expanded_cme_df.rename(columns={'startTime':'startTime_CME','activityID':'cmeID'}, inplace=True)

# Drop linkedEvents
expanded_cme_df.drop(columns=['linkedEvents'], inplace=True)

# Verify that all steps were executed correctly
expanded_cme_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 337 entries, 0 to 336
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype              
---  ------          --------------  -----              
 0   cmeID           337 non-null    object             
 1   startTime_CME   337 non-null    datetime64[ns, UTC]
 2   GST_ActivityID  337 non-null    object             
dtypes: datetime64[ns, UTC](1), object(2)
memory usage: 8.0+ KB


In [481]:
# We are only interested in CMEs related to GSTs so keep only rows where the GST_ActivityID column contains 'GST'
# use the method 'contains()' from the str library.  
cleaned_cme_df = expanded_cme_df[expanded_cme_df['GST_ActivityID'].str.contains('GST')]
cleaned_cme_df.reset_index(drop=True, inplace=True)
cleaned_cme_df.info()
cleaned_cme_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10 entries, 0 to 9
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype              
---  ------          --------------  -----              
 0   cmeID           10 non-null     object             
 1   startTime_CME   10 non-null     datetime64[ns, UTC]
 2   GST_ActivityID  10 non-null     object             
dtypes: datetime64[ns, UTC](1), object(2)
memory usage: 372.0+ bytes


cmeID             startTime_CME  \
0  2013-06-02T20:24:00-CME-001 2013-06-02 20:24:00+00:00   
1  2013-09-29T22:40:00-CME-001 2013-09-29 22:40:00+00:00   
2  2013-12-04T23:12:00-CME-001 2013-12-04 23:12:00+00:00   
3  2014-02-16T14:15:00-CME-001 2014-02-16 14:15:00+00:00   
4  2014-02-18T01:25:00-CME-001 2014-02-18 01:25:00+00:00   

                GST_ActivityID  
0  2013-06-07T03:00:00-GST-001  
1  2013-10-02T03:00:00-GST-001  
2  2013-12-08T00:00:00-GST-001  
3  2014-02-19T03:00:00-GST-001  
4  2014-02-20T03:00:00-GST-001

### GST Data

In [423]:
# Set the base URL to NASA's DONKI API:
base_url = "https://api.nasa.gov/DONKI/"

# Set the specifier for Geomagnetic Storms (GST):
GST = "GST"

# Search for GSTs between a begin and end date
startDate = "2013-05-01"
endDate   = "2015-05-01"

# Build URL for GST
#https://api.nasa.gov/DONKI/GST?startDate=yyyy-MM-dd&endDate=yyyy-MM-dd&api_key=DEMO_KEY
gst_query_url = f"{base_url}{GST}?startDate={startDate}&endDate={endDate}&api_key={NASA_API_KEY}"
print(gst_query_url)

https://api.nasa.gov/DONKI/GST?startDate=2013-05-01&endDate=2015-05-01&api_key=v3cb6u2K4SofJWUFcnupS80ZgFMhbT0iGHo9nPBf


In [424]:
# Make a "GET" request for the GST URL and store it in a variable named gst_response
gst_response = requests.get(gst_query_url)

In [425]:
# Convert the response variable to json and store it as a variable named gst_json
gst_json = gst_response.json()
# Preview the first result in JSON format
# Use json.dumps with argument indent=4 to format data
print(json.dumps(gst_json, indent=4))

[
    {
        "gstID": "2013-06-01T01:00:00-GST-001",
        "startTime": "2013-06-01T01:00Z",
        "allKpIndex": [
            {
                "observedTime": "2013-06-01T01:00Z",
                "kpIndex": 6.0,
                "source": "NOAA"
            }
        ],
        "link": "https://webtools.ccmc.gsfc.nasa.gov/DONKI/view/GST/326/-1",
        "linkedEvents": [
            {
                "activityID": "2013-05-31T15:45:00-HSS-001"
            }
        ],
        "submissionTime": "2013-07-15T19:26Z",
        "versionId": 1
    },
    {
        "gstID": "2013-06-07T03:00:00-GST-001",
        "startTime": "2013-06-07T03:00Z",
        "allKpIndex": [
            {
                "observedTime": "2013-06-07T03:00Z",
                "kpIndex": 6.0,
                "source": "NOAA"
            }
        ],
        "link": "https://webtools.ccmc.gsfc.nasa.gov/DONKI/view/GST/330/-1",
        "linkedEvents": [
            {
                "activityID": "2013-06-02T20:24:

In [426]:
# Convert gst_json to a Pandas DataFrame  
gst_df = pd.DataFrame(gst_json)
# Keep only the columns: activityID, startTime, linkedEvents
gst_df = gst_df[['gstID','startTime','linkedEvents']]
gst_df.info()
gst_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16 entries, 0 to 15
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   gstID         16 non-null     object
 1   startTime     16 non-null     object
 2   linkedEvents  13 non-null     object
dtypes: object(3)
memory usage: 516.0+ bytes


gstID          startTime  \
0  2013-06-01T01:00:00-GST-001  2013-06-01T01:00Z   
1  2013-06-07T03:00:00-GST-001  2013-06-07T03:00Z   
2  2013-06-29T03:00:00-GST-001  2013-06-29T03:00Z   
3  2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
4  2013-12-08T00:00:00-GST-001  2013-12-08T00:00Z   

                                        linkedEvents  
0    [{'activityID': '2013-05-31T15:45:00-HSS-001'}]  
1    [{'activityID': '2013-06-02T20:24:00-CME-001'}]  
2                                               None  
3  [{'activityID': '2013-09-29T22:40:00-CME-001'}...  
4  [{'activityID': '2013-12-04T23:12:00-CME-001'}...

In [447]:
# Notice that the linkedEvents column allows us to identify the corresponding CME
# Remove rows with missing 'linkedEvents' since we won't be able to assign these to CME
gst_df.dropna(subset=['linkedEvents'], inplace=True)
gst_df.info()
gst_df.head()

<class 'pandas.core.frame.DataFrame'>
Index: 13 entries, 0 to 13
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   gstID         13 non-null     object
 1   startTime     13 non-null     object
 2   linkedEvents  13 non-null     object
dtypes: object(3)
memory usage: 416.0+ bytes


gstID          startTime  \
0  2013-06-01T01:00:00-GST-001  2013-06-01T01:00Z   
1  2013-06-07T03:00:00-GST-001  2013-06-07T03:00Z   
3  2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
4  2013-12-08T00:00:00-GST-001  2013-12-08T00:00Z   
5  2014-02-19T03:00:00-GST-001  2014-02-19T03:00Z   

                                        linkedEvents  
0    [{'activityID': '2013-05-31T15:45:00-HSS-001'}]  
1    [{'activityID': '2013-06-02T20:24:00-CME-001'}]  
3  [{'activityID': '2013-09-29T22:40:00-CME-001'}...  
4  [{'activityID': '2013-12-04T23:12:00-CME-001'}...  
5  [{'activityID': '2014-02-16T14:15:00-CME-001'}...

In [448]:
# Notice that the linkedEvents sometimes contains multiple events per row
# Use the explode method to ensure that each row is one element. Ensure to reset the index and drop missing values.
expanded_gst_df = gst_df.explode(['linkedEvents'])
expanded_gst_df.reset_index(drop=True, inplace=True)
expanded_gst_df.info()
expanded_gst_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27 entries, 0 to 26
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   gstID         27 non-null     object
 1   startTime     27 non-null     object
 2   linkedEvents  27 non-null     object
dtypes: object(3)
memory usage: 780.0+ bytes


gstID          startTime  \
0  2013-06-01T01:00:00-GST-001  2013-06-01T01:00Z   
1  2013-06-07T03:00:00-GST-001  2013-06-07T03:00Z   
2  2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
3  2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
4  2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   

                                    linkedEvents  
0  {'activityID': '2013-05-31T15:45:00-HSS-001'}  
1  {'activityID': '2013-06-02T20:24:00-CME-001'}  
2  {'activityID': '2013-09-29T22:40:00-CME-001'}  
3  {'activityID': '2013-10-02T01:54:00-IPS-001'}  
4  {'activityID': '2013-10-02T02:47:00-MPC-001'}

In [449]:
# Apply the extract_activityID_from_dict function to each row in the 'linkedEvents' column (you can use apply() and a lambda function)
# and create a new column called 'CME_ActivityID' using loc indexer:
expanded_gst_df['CME_ActivityID'] = expanded_gst_df['linkedEvents'].apply(extract_activityID_from_dict)
expanded_gst_df

# Remove rows with missing CME_ActivityID, since we can't assign them to CMEs:
expanded_gst_df.dropna(subset=['CME_ActivityID'], inplace=True)
expanded_gst_df


gstID          startTime  \
0   2013-06-01T01:00:00-GST-001  2013-06-01T01:00Z   
1   2013-06-07T03:00:00-GST-001  2013-06-07T03:00Z   
2   2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
3   2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
4   2013-10-02T03:00:00-GST-001  2013-10-02T03:00Z   
5   2013-12-08T00:00:00-GST-001  2013-12-08T00:00Z   
6   2013-12-08T00:00:00-GST-001  2013-12-08T00:00Z   
7   2014-02-19T03:00:00-GST-001  2014-02-19T03:00Z   
8   2014-02-19T03:00:00-GST-001  2014-02-19T03:00Z   
9   2014-02-20T03:00:00-GST-001  2014-02-20T03:00Z   
10  2014-02-20T03:00:00-GST-001  2014-02-20T03:00Z   
11  2014-02-20T03:00:00-GST-001  2014-02-20T03:00Z   
12  2014-02-27T18:00:00-GST-001  2014-02-27T18:00Z   
13  2014-02-27T18:00:00-GST-001  2014-02-27T18:00Z   
14  2014-06-08T03:00:00-GST-001  2014-06-08T03:00Z   
15  2014-06-08T03:00:00-GST-001  2014-06-08T03:00Z   
16  2014-06-08T03:00:00-GST-001  2014-06-08T03:00Z   
17  2014-08-19T21:00:00-GST-001  2014-08-19T21:00Z   
18  2014-08-19T21:00:00-GST-001  2014-08-19T21:00Z   
19  2014-09-12T15:00:00-GST-001  2014-09-12T15:00Z   
20  2014-09-12T15:00:00-GST-001  2014-09-12T15:00Z   
21  2015-01-07T06:00:00-GST-001  2015-01-07T06:00Z   
22  2015-01-07T06:00:00-GST-001  2015-01-07T06:00Z   
23  2015-03-17T06:00:00-GST-001  2015-03-17T06:00Z   
24  2015-03-17T06:00:00-GST-001  2015-03-17T06:00Z   
25  2015-03-17T06:00:00-GST-001  2015-03-17T06:00Z   
26  2015-03-22T06:00:00-GST-001  2015-03-22T06:00Z   

                                     linkedEvents               CME_ActivityID  
0   {'activityID': '2013-05-31T15:45:00-HSS-001'}  2013-05-31T15:45:00-HSS-001  
1   {'activityID': '2013-06-02T20:24:00-CME-001'}  2013-06-02T20:24:00-CME-001  
2   {'activityID': '2013-09-29T22:40:00-CME-001'}  2013-09-29T22:40:00-CME-001  
3   {'activityID': '2013-10-02T01:54:00-IPS-001'}  2013-10-02T01:54:00-IPS-001  
4   {'activityID': '2013-10-02T02:47:00-MPC-001'}  2013-10-02T02:47:00-MPC-001  
5   {'activityID': '2013-12-04T23:12:00-CME-001'}  2013-12-04T23:12:00-CME-001  
6   {'activityID': '2013-12-07T21:30:00-HSS-001'}  2013-12-07T21:30:00-HSS-001  
7   {'activityID': '2014-02-16T14:15:00-CME-001'}  2014-02-16T14:15:00-CME-001  
8   {'activityID': '2014-02-19T03:10:00-IPS-001'}  2014-02-19T03:10:00-IPS-001  
9   {'activityID': '2014-02-18T01:25:00-CME-001'}  2014-02-18T01:25:00-CME-001  
10  {'activityID': '2014-02-20T02:50:00-IPS-001'}  2014-02-20T02:50:00-IPS-001  
11  {'activityID': '2014-02-20T05:14:00-MPC-001'}  2014-02-20T05:14:00-MPC-001  
12  {'activityID': '2014-02-25T01:25:00-CME-001'}  2014-02-25T01:25:00-CME-001  
13  {'activityID': '2014-02-27T16:10:00-IPS-001'}  2014-02-27T16:10:00-IPS-001  
14  {'activityID': '2014-06-04T13:25:00-CME-001'}  2014-06-04T13:25:00-CME-001  
15  {'activityID': '2014-06-07T16:09:00-IPS-001'}  2014-06-07T16:09:00-IPS-001  
16  {'activityID': '2014-06-08T05:08:00-MPC-001'}  2014-06-08T05:08:00-MPC-001  
17  {'activityID': '2014-08-15T21:12:00-CME-001'}  2014-08-15T21:12:00-CME-001  
18  {'activityID': '2014-08-19T05:57:00-IPS-001'}  2014-08-19T05:57:00-IPS-001  
19  {'activityID': '2014-09-10T18:18:00-CME-001'}  2014-09-10T18:18:00-CME-001  
20  {'activityID': '2014-09-12T15:26:00-IPS-001'}  2014-09-12T15:26:00-IPS-001  
21  {'activityID': '2015-01-07T05:24:00-IPS-001'}  2015-01-07T05:24:00-IPS-001  
22  {'activityID': '2015-01-07T08:40:00-MPC-001'}  2015-01-07T08:40:00-MPC-001  
23  {'activityID': '2015-03-15T02:00:00-CME-001'}  2015-03-15T02:00:00-CME-001  
24  {'activityID': '2015-03-17T04:05:00-IPS-001'}  2015-03-17T04:05:00-IPS-001  
25  {'activityID': '2015-03-16T00:00:00-HSS-001'}  2015-03-16T00:00:00-HSS-001  
26  {'activityID': '2015-03-21T20:25:00-IPS-001'}  2015-03-21T20:25:00-IPS-001

In [450]:
# Convert the 'CME_ActivityID' column to string format 
expanded_gst_df['CME_ActivityID'] = expanded_gst_df['CME_ActivityID'].astype(str)

# Convert the 'gstID' column to string format 
expanded_gst_df['gstID'] = expanded_gst_df['gstID'].astype('string')

# Convert startTime to datetime format  
expanded_gst_df['startTime'] = pd.to_datetime(expanded_gst_df['startTime'])

# Rename startTime to startTime_GST 
expanded_gst_df.rename(columns={'startTime':'startTime_GST'}, inplace=True)

# Drop linkedEvents
expanded_gst_df.drop(columns=['linkedEvents'], inplace=True)

# Verify that all steps were executed correctly
expanded_gst_df.info()



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27 entries, 0 to 26
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype              
---  ------          --------------  -----              
 0   gstID           27 non-null     string             
 1   startTime_GST   27 non-null     datetime64[ns, UTC]
 2   CME_ActivityID  27 non-null     object             
dtypes: datetime64[ns, UTC](1), object(1), string(1)
memory usage: 780.0+ bytes


In [451]:
# We are only interested in GSTs related to CMEs so keep only rows where the CME_ActivityID column contains 'CME'
# use the method 'contains()' from the str library.  
cleaned_gst_df = expanded_gst_df[expanded_gst_df['CME_ActivityID'].str.contains('CME')]
cleaned_gst_df.head()


gstID             startTime_GST  \
1  2013-06-07T03:00:00-GST-001 2013-06-07 03:00:00+00:00   
2  2013-10-02T03:00:00-GST-001 2013-10-02 03:00:00+00:00   
5  2013-12-08T00:00:00-GST-001 2013-12-08 00:00:00+00:00   
7  2014-02-19T03:00:00-GST-001 2014-02-19 03:00:00+00:00   
9  2014-02-20T03:00:00-GST-001 2014-02-20 03:00:00+00:00   

                CME_ActivityID  
1  2013-06-02T20:24:00-CME-001  
2  2013-09-29T22:40:00-CME-001  
5  2013-12-04T23:12:00-CME-001  
7  2014-02-16T14:15:00-CME-001  
9  2014-02-18T01:25:00-CME-001

### Merge both datatsets

In [456]:
print("Unique values in cleaned_gst_df['CME_ActivityID']:", cleaned_gst_df['CME_ActivityID'].unique())
print("Unique values in cleaned_cme_df['GST_ActivityID']:", cleaned_cme_df['GST_ActivityID'].unique())

Unique values in cleaned_gst_df['CME_ActivityID']: ['2013-06-02T20:24:00-CME-001' '2013-09-29T22:40:00-CME-001'
 '2013-12-04T23:12:00-CME-001' '2014-02-16T14:15:00-CME-001'
 '2014-02-18T01:25:00-CME-001' '2014-02-25T01:25:00-CME-001'
 '2014-06-04T13:25:00-CME-001' '2014-08-15T21:12:00-CME-001'
 '2014-09-10T18:18:00-CME-001' '2015-03-15T02:00:00-CME-001']
Unique values in cleaned_cme_df['GST_ActivityID']: ['2013-06-07T03:00:00-GST-001' '2013-10-02T03:00:00-GST-001'
 '2013-12-08T00:00:00-GST-001' '2014-02-19T03:00:00-GST-001'
 '2014-02-20T03:00:00-GST-001' '2014-02-27T18:00:00-GST-001'
 '2014-06-08T03:00:00-GST-001' '2014-08-19T21:00:00-GST-001'
 '2014-09-12T15:00:00-GST-001' '2015-03-17T06:00:00-GST-001']


In [482]:
# Now merge both datasets using 'gstID' and 'CME_ActivityID' for gst and 'GST_ActivityID' and 'cmeID' for cme. Use the 'left_on' and 'right_on' specifiers.
merged_df = pd.merge(
    cleaned_gst_df, cleaned_cme_df, 
    left_on=['gstID', 'CME_ActivityID'],
    right_on=['GST_ActivityID','cmeID'],
    how='inner'
)
merged_df

gstID             startTime_GST  \
0  2013-06-07T03:00:00-GST-001 2013-06-07 03:00:00+00:00   
1  2013-10-02T03:00:00-GST-001 2013-10-02 03:00:00+00:00   
2  2013-12-08T00:00:00-GST-001 2013-12-08 00:00:00+00:00   
3  2014-02-19T03:00:00-GST-001 2014-02-19 03:00:00+00:00   
4  2014-02-20T03:00:00-GST-001 2014-02-20 03:00:00+00:00   
5  2014-02-27T18:00:00-GST-001 2014-02-27 18:00:00+00:00   
6  2014-06-08T03:00:00-GST-001 2014-06-08 03:00:00+00:00   
7  2014-08-19T21:00:00-GST-001 2014-08-19 21:00:00+00:00   
8  2014-09-12T15:00:00-GST-001 2014-09-12 15:00:00+00:00   
9  2015-03-17T06:00:00-GST-001 2015-03-17 06:00:00+00:00   

                CME_ActivityID                        cmeID  \
0  2013-06-02T20:24:00-CME-001  2013-06-02T20:24:00-CME-001   
1  2013-09-29T22:40:00-CME-001  2013-09-29T22:40:00-CME-001   
2  2013-12-04T23:12:00-CME-001  2013-12-04T23:12:00-CME-001   
3  2014-02-16T14:15:00-CME-001  2014-02-16T14:15:00-CME-001   
4  2014-02-18T01:25:00-CME-001  2014-02-18T01:25:00-CME-001   
5  2014-02-25T01:25:00-CME-001  2014-02-25T01:25:00-CME-001   
6  2014-06-04T13:25:00-CME-001  2014-06-04T13:25:00-CME-001   
7  2014-08-15T21:12:00-CME-001  2014-08-15T21:12:00-CME-001   
8  2014-09-10T18:18:00-CME-001  2014-09-10T18:18:00-CME-001   
9  2015-03-15T02:00:00-CME-001  2015-03-15T02:00:00-CME-001   

              startTime_CME               GST_ActivityID  
0 2013-06-02 20:24:00+00:00  2013-06-07T03:00:00-GST-001  
1 2013-09-29 22:40:00+00:00  2013-10-02T03:00:00-GST-001  
2 2013-12-04 23:12:00+00:00  2013-12-08T00:00:00-GST-001  
3 2014-02-16 14:15:00+00:00  2014-02-19T03:00:00-GST-001  
4 2014-02-18 01:25:00+00:00  2014-02-20T03:00:00-GST-001  
5 2014-02-25 01:25:00+00:00  2014-02-27T18:00:00-GST-001  
6 2014-06-04 13:25:00+00:00  2014-06-08T03:00:00-GST-001  
7 2014-08-15 21:12:00+00:00  2014-08-19T21:00:00-GST-001  
8 2014-09-10 18:18:00+00:00  2014-09-12T15:00:00-GST-001  
9 2015-03-15 02:00:00+00:00  2015-03-17T06:00:00-GST-001

In [483]:
# Verify that the new DataFrame has the same number of rows as cme and gst
merged_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10 entries, 0 to 9
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype              
---  ------          --------------  -----              
 0   gstID           10 non-null     object             
 1   startTime_GST   10 non-null     datetime64[ns, UTC]
 2   CME_ActivityID  10 non-null     object             
 3   cmeID           10 non-null     object             
 4   startTime_CME   10 non-null     datetime64[ns, UTC]
 5   GST_ActivityID  10 non-null     object             
dtypes: datetime64[ns, UTC](2), object(4)
memory usage: 612.0+ bytes


### Computing the time it takes for a CME to cause a GST

In [486]:
# Compute the time diff between startTime_GST and startTime_CME by creating a new column called `timeDiff`.
merged_df['timeDiff'] = merged_df['startTime_GST'] - merged_df['startTime_CME']
merged_df

gstID             startTime_GST  \
0  2013-06-07T03:00:00-GST-001 2013-06-07 03:00:00+00:00   
1  2013-10-02T03:00:00-GST-001 2013-10-02 03:00:00+00:00   
2  2013-12-08T00:00:00-GST-001 2013-12-08 00:00:00+00:00   
3  2014-02-19T03:00:00-GST-001 2014-02-19 03:00:00+00:00   
4  2014-02-20T03:00:00-GST-001 2014-02-20 03:00:00+00:00   
5  2014-02-27T18:00:00-GST-001 2014-02-27 18:00:00+00:00   
6  2014-06-08T03:00:00-GST-001 2014-06-08 03:00:00+00:00   
7  2014-08-19T21:00:00-GST-001 2014-08-19 21:00:00+00:00   
8  2014-09-12T15:00:00-GST-001 2014-09-12 15:00:00+00:00   
9  2015-03-17T06:00:00-GST-001 2015-03-17 06:00:00+00:00   

                CME_ActivityID                        cmeID  \
0  2013-06-02T20:24:00-CME-001  2013-06-02T20:24:00-CME-001   
1  2013-09-29T22:40:00-CME-001  2013-09-29T22:40:00-CME-001   
2  2013-12-04T23:12:00-CME-001  2013-12-04T23:12:00-CME-001   
3  2014-02-16T14:15:00-CME-001  2014-02-16T14:15:00-CME-001   
4  2014-02-18T01:25:00-CME-001  2014-02-18T01:25:00-CME-001   
5  2014-02-25T01:25:00-CME-001  2014-02-25T01:25:00-CME-001   
6  2014-06-04T13:25:00-CME-001  2014-06-04T13:25:00-CME-001   
7  2014-08-15T21:12:00-CME-001  2014-08-15T21:12:00-CME-001   
8  2014-09-10T18:18:00-CME-001  2014-09-10T18:18:00-CME-001   
9  2015-03-15T02:00:00-CME-001  2015-03-15T02:00:00-CME-001   

              startTime_CME               GST_ActivityID        timeDiff  
0 2013-06-02 20:24:00+00:00  2013-06-07T03:00:00-GST-001 4 days 06:36:00  
1 2013-09-29 22:40:00+00:00  2013-10-02T03:00:00-GST-001 2 days 04:20:00  
2 2013-12-04 23:12:00+00:00  2013-12-08T00:00:00-GST-001 3 days 00:48:00  
3 2014-02-16 14:15:00+00:00  2014-02-19T03:00:00-GST-001 2 days 12:45:00  
4 2014-02-18 01:25:00+00:00  2014-02-20T03:00:00-GST-001 2 days 01:35:00  
5 2014-02-25 01:25:00+00:00  2014-02-27T18:00:00-GST-001 2 days 16:35:00  
6 2014-06-04 13:25:00+00:00  2014-06-08T03:00:00-GST-001 3 days 13:35:00  
7 2014-08-15 21:12:00+00:00  2014-08-19T21:00:00-GST-001 3 days 23:48:00  
8 2014-09-10 18:18:00+00:00  2014-09-12T15:00:00-GST-001 1 days 20:42:00  
9 2015-03-15 02:00:00+00:00  2015-03-17T06:00:00-GST-001 2 days 04:00:00

In [487]:
# Use describe() to compute the mean and median time 
# that it takes for a CME to cause a GST. 
merged_df['timeDiff'].describe()

count                           10
mean               2 days 20:04:24
std      0 days 20:24:43.751673414
min                1 days 20:42:00
25%                2 days 04:05:00
50%                2 days 14:40:00
75%                3 days 10:23:15
max                4 days 06:36:00
Name: timeDiff, dtype: object

### Exporting data in csv format

In [490]:
# Export data to CSV without the index
merged_df.to_csv('../data-sourcing-challenge/cme_gst_merged_data.csv', index=False)